In [1]:
%%bash

pip install jupyterthemes

You should consider upgrading via the '/home/ec2-user/anaconda3/envs/python3/bin/python -m pip install --upgrade pip' command.


In [2]:
# c = get_config()  # jupyter has this built-in function
# c.NotebookApp.iopub_data_rate_limit = 1.0e42

In [3]:
# create a darker background template (better for my eyes)
from jupyterthemes.stylefx import set_nb_theme
set_nb_theme('chesterish')

In [4]:
# console and directory access
import os
import re
import shutil
import datetime

# interacting with Amazon AWS
import boto3
from sagemaker.session import Session

# data reading and exporting  
import json
import tempfile
import pandas as pd
import numpy as np
import struct

# parsing SEC website for data  
import requests
import time 
from bs4 import BeautifulSoup
from urllib.request import Request, urlopen

In [5]:
file_type = 'X-17A-5'       # files looking to extract
prior2date = '20201231'     # format YYYY/MM/DD - select data prior to this data

In [6]:
bucket = "ran-s3-systemic-risk"
data_folder ="Input/X-17A-5/"

# Amazon Textract client and Sagemaker session
s3 = boto3.client('s3')
session = Session()

In [7]:
os.getcwd()

'/home/ec2-user/SageMaker/SEC_X17A5'

## Dealer Data Import
Parses in dealer information with accompaning CIK code for EDGAR lookup from the SEC dealer registration

In [8]:
if os.path.isfile('CIKandDealers.txt'):
    print('Broker dealer data has been found')
    
    # exporting RegisteredDealer information, loading in JSON dictionary 
    with open('CIKandDealers.txt') as file:
        cik2brokers = json.load(file)
    
    # unpacking the dictionary keys (all broker dealer CIK figures)
    bdNames = [*cik2brokers]
else:
    print('File not found, retrieving information ...')
    start = time.time()
    
    # will be used to concat all available broker dealer information 
    tempDF = []
    
    # send request to SEC website to retrieve broker dealer information 
    response = requests.get('https://www.sec.gov/help/foiadocsbdfoiahtm.html', allow_redirects=True)

    # parse the HTML doc string from the response object
    s1Table = BeautifulSoup(response.text, 'html.parser') 
    
    # parse through links from the SEC filings
    for link in s1Table.find_all('a'):
        documentURL = link.get('href')           # document links for filings
        
        try:
            # find .txt file substring greater than 0
            if documentURL.find('.txt') > 0:
                
                # requesting data from document links storing the files
                pdf_storage = requests.get('https://www.sec.gov'+ documentURL, allow_redirects=True)
                
                # open a file to store files from SEC
                open('secDealers.txt', 'wb').write(pdf_storage.content)
                
                # convert text file to .csv and store dataframe
                df = pd.read_csv('secDealers.txt', sep="\t", header=None)
                
                dateRelease = documentURL.split('/')[-1][2:-4]
                print('\tSEC Dealer information has been downloaded ' + dateRelease)
                
                # append new dataframe figures to be concated
                tempDF.append(df)
                
        except AttributeError:
            pass
    
    # concat all disjoint dataframes
    df = pd.concat(tempDF)
    
    # remove NaN columns and provide column naming conventions
    df = df[df.columns[:-1]]
    df.columns = ['CIK NUMBER', 'COMPANY NAME', 'REPORTING FILE NUMBER', 'ADDRESS1',
                  'ADDRESS2', 'CITY', 'STATE CODE', 'ZIP CODE']
    
    # remove duplicate rows from the dataset
    df = df.drop_duplicates(subset='CIK NUMBER')
    df.to_csv('secRegisteredDealers.csv')

    # convert CIK and Company Name to dictionary
    cik2brokers = df[df.columns[:2]].set_index('CIK NUMBER').to_dict(orient='index')

    # unpacking the dictionary keys (all broker dealer CIK figures)
    bdNames = [*cik2brokers]

    # exporting RegisteredDealer information
    with open('CIKandDealers.txt', 'w') as file:
        json.dump(cik2brokers, file)
        file.close()
    
    print('Time taken is {} seconds'.format(time.time()-start))

Broker dealer data has been found


### Archived Dealer Data
Archived SEC broker dealer CIKs since 1993 per quarter 

In [163]:
def companyName(cik) -> str:
    """
    Returns the company name for a given CIK number from the SEC
    """
    baseURL = 'https://www.sec.gov/cgi-bin/browse-edgar?action=getcompany&'
    url = baseURL+'CIK={}&type=X-17A-5&dateb=20201231'.format(cik)
    
    # response time for retrieving company names, returning beautifulsoup object
    res = requests.get(url, allow_redirects=True)
    s1 = BeautifulSoup(res.text, 'html.parser')
    
    # select the company name from the SEC website for a particular CIK
    for val in s1.find_all('span', attrs={"class":"companyName"}):
        return val.text.split('CIK')[0].split('/BD')[0]

In [164]:
# additional archived data pre-2007 is stored at https://www.sec.gov/Archives/edgar/full-index/
baseURL = 'https://www.sec.gov/Archives/edgar/full-index/'
years = np.arange(1993, datetime.datetime.today().year+1)
quarters = ['QTR1', 'QTR2', 'QTR3', 'QTR4']

# itterate through years and quarters
for year in years:
    for qt in quarters:
        searchURL = '{}{}/{}/form.idx'.format(baseURL, year, qt)
        print(searchURL)

        # send request to SEC website to retrieve broker dealer information 
        response = requests.get(searchURL, allow_redirects=True)
        data = response.text.split('---')[-1]   # extract only main text from body
        
        # write contents to a temporary file
        with open('main.txt', 'w') as file: file.write(data)

        # convert text data to dataframe object and search for files
        df = pd.read_fwf('main.txt', header=None)
        df = df.dropna(axis=0)
        
        # check to see if first column contains information on X-17A-5 filings
        check = df[0].str.contains('^x-17a', regex=True, flags=re.IGNORECASE)
        xFile = df[check]
        
        # check whether X-17A-5 was found
        if not xFile.empty:
            # cik number is taken from the last column of the rows splitting url string 
            cikNumbers = xFile[xFile.columns[-1]].apply(lambda x: x.split('/')[2]).values
            
            for elm in cikNumbers:
                # if CIK not in bdName then we append new series
                if elm not in bdNames:
                    compName = companyName(elm)   # company name for CIK
                    cik2brokers[elm] = {'COMPANY NAME' : compName}
        
        # remove local file after it has been created
        os.remove('main.txt')

https://www.sec.gov/Archives/edgar/full-index/1993/QTR1/form.idx
https://www.sec.gov/Archives/edgar/full-index/1993/QTR2/form.idx
https://www.sec.gov/Archives/edgar/full-index/1993/QTR3/form.idx
https://www.sec.gov/Archives/edgar/full-index/1993/QTR4/form.idx
https://www.sec.gov/Archives/edgar/full-index/1994/QTR1/form.idx
https://www.sec.gov/Archives/edgar/full-index/1994/QTR2/form.idx
https://www.sec.gov/Archives/edgar/full-index/1994/QTR3/form.idx
https://www.sec.gov/Archives/edgar/full-index/1994/QTR4/form.idx
https://www.sec.gov/Archives/edgar/full-index/1995/QTR1/form.idx
https://www.sec.gov/Archives/edgar/full-index/1995/QTR2/form.idx
https://www.sec.gov/Archives/edgar/full-index/1995/QTR3/form.idx
https://www.sec.gov/Archives/edgar/full-index/1995/QTR4/form.idx
https://www.sec.gov/Archives/edgar/full-index/1996/QTR1/form.idx
https://www.sec.gov/Archives/edgar/full-index/1996/QTR2/form.idx
https://www.sec.gov/Archives/edgar/full-index/1996/QTR3/form.idx
https://www.sec.gov/Archi

In [168]:
# exporting RegisteredDealer information
with open('CIKandDealers.txt', 'w') as file:
    json.dump(cik2brokers, file)
    file.close()

In [170]:
bdNames = [*cik2brokers]

In [9]:
# sample of CIK brokers & dealer retained from SEC directory (orginal=7904; post-sec=9730)
pd.DataFrame.from_dict(cik2brokers, orient='index').reset_index().sort_values(by='COMPANY NAME')

index                              COMPANY NAME
5495  1647385                             16 POINTS LLC
7706    80869           1717 CAPITAL MANAGEMENT COMPANY
4203  1421259                      1792 SECURITIES, LLC
5747  1721381                180 DEGREE CAPITAL BD, LLC
4720  1482939                      1851 SECURITIES, INC
...       ...                                       ...
5221  1571109                           ZOO TRADING LLC
9675   948394                   ZPG SECURITIES, L.L.C. 
446   1028769  ZURICH CAPITAL MARKETS SECURITIES, INC. 
7669   805290                       ZYDECO TRADING, LLC
5693  1707588                    ZYNCAP SECURITIES, LLC

[9730 rows x 2 columns]

## PDF File Extraction
Extract URL links per company filing to download accompaning X-17A-5 files from SEC EDGAR site

In [9]:
n = len(bdNames)                # number of broker/dealers
secURLS = [0]*n                 # initialize memory 
startTime = time.time()         # set tuner to track code 
completeYear = None             # initialize year to check for updates

secFormat = 'https://www.sec.gov/cgi-bin/browse-edgar?'     # SEC base url
dataSelect = 'action=getcompany&CIK={}&type={}&dateb={}'    # select params.
    
# iterate through the CIK's from the broker dealers to build lookup URLs
for name in range(n):       
    url = secFormat + dataSelect.format(bdNames[name], file_type, prior2date)
    secURLS[name] = url                     # storing the search URLs

In [10]:
# created SEC URLs that will be used for lookup
np.array(secURLS)

array(['https://www.sec.gov/cgi-bin/browse-edgar?action=getcompany&CIK=1904&type=X-17A-5&dateb=20201231',
       'https://www.sec.gov/cgi-bin/browse-edgar?action=getcompany&CIK=2303&type=X-17A-5&dateb=20201231',
       'https://www.sec.gov/cgi-bin/browse-edgar?action=getcompany&CIK=2554&type=X-17A-5&dateb=20201231',
       ...,
       'https://www.sec.gov/cgi-bin/browse-edgar?action=getcompany&CIK=1049379&type=X-17A-5&dateb=20201231',
       'https://www.sec.gov/cgi-bin/browse-edgar?action=getcompany&CIK=1218191&type=X-17A-5&dateb=20201231',
       'https://www.sec.gov/cgi-bin/browse-edgar?action=getcompany&CIK=1736877&type=X-17A-5&dateb=20201231'],
      dtype='<U98')

In [11]:
def edgarParse(url:str):
    """
    Parses the EDGAR webpage of a provided URL and returns a tuple of arrays/lists
    
    Input:
        url is a string, representing a SEC website URL 

    Return:
        filing_dates is a vector of date strings for all X-17A-5 filings
        archives is a vector of strings for all sec.gov URL links for each filings
    """
    
    # requesting HTML data link from the EDGAR search results 
    response = requests.get(url, allow_redirects=True)

    # parse the HTML doc string from the response object
    soup = BeautifulSoup(response.text, 'html.parser') 
    
    try:
        # read in HTML tables from the url link provided 
        filings = pd.read_html(url)[2]                 # select the filings table
        filing_dates = filings['Filing Date'].values   # return the filing dates

        # parse the html-doc string for all instance of < a href= >
        href = [link.get('href') for link in soup.find_all('a')]

        # search for all links with Archive in handle, these are the search links for the X-17A-5 filings
        archives = ['https://www.sec.gov' + link for link in href if str.find(link, 'Archives') > 0]
        
        return filing_dates, archives
    
    except IndexError:
        print('Currently no filings are present\n')
        

In [12]:
def fileExtract(secURLS:list, cik2brokers:dict, bdNames:list, subFolder:str='Input/X-17A-5/', 
                file_type:str='X-17A-5', bucket:str='ran-s3-systemic-risk', flag=True):
    """
    Parses through the pdf links X-17A-5 pdf files to be saved in an s3 bucket
    
    NOTE:   This script makes no effort to weed out amended releases, rather it will default to retaing 
            information on first published releases via iterative retention 
    """
    n = len(bdNames)
    
    # discover all of the pdfs that you want to parse
    s3_path = session.list_s3_files(bucket, subFolder)
    
    # initialize time for process to run 
    startTime = time.time()
    
    # the URL links for each SEC company
    for index in range(n):
        
        try:
            # return the filing dates and archived url's for each SEC company 
            filing_dates, archives = edgarParse(secURLS[index])

            # company name for broker dealer being downloaded
            companyName = cik2brokers[bdNames[index]]['COMPANY NAME']

            # logging info for when files are being downloaded
            print('{} - Downloading {} files for {} - CIK ({})'.format(index, file_type, companyName, bdNames[index]))

            # itterate through each of the pdf urls corresponding to archived contents
            for i, pdf_url in enumerate(archives):

                # filing year in full yyyy-MM-dd format, extracting yyyy portion 
                year = filing_dates[i][:4]

                # data is organized linearly, by most recent issue first
                # requesting data from document links storing the files
                pdf_storage = requests.get(pdf_url, allow_redirects=True)

                # table from filing detail Edgar table 
                soup = BeautifulSoup(pdf_storage.text, 'html.parser') 

                # extracts all link within the filing table, filtering for pdfs
                extract_link = [file.get('href') for file in soup.find_all('a')]

                # filter for all pdf links from the extracted file links  
                pdf_files = [string for string in extract_link if str.find(string, 'pdf') > 0]

                # check to see if a pdf file exists to extract, otherwise move on 
                try:
                    # our pdf file of interst tends to be the last pdf in the list (we index -1 for last)
                    pdf_file = 'https://www.sec.gov' + pdf_files[-1] 
                    pdf_name = subFolder + str(bdNames[index]) + '-' + year + '.pdf'

                    # flag boolean gives user option to be efficient or thorough
                    # if pdf_name exists in s3 bucket simply continue to other company, we assume all previous files are present
                    if (pdf_name in s3_path) & (flag == True): 
                        print('\tAll files for {} are downloaded'.format(companyName))
                        break

                    else:
                        # request the specific pdf file from the the SEC
                        pdf_storage = requests.get(pdf_file, allow_redirects=True)

                        # filename for the pdf to be stored in s3
                        fileName = str(bdNames[index]) + '-' +  year + '.pdf'

                        # save PDF contents to local file location 
                        open(fileName, 'wb').write(pdf_storage.content)

                        # save contents to AWS S3 bucket
                        with open(fileName, 'rb') as data:
                            s3.upload_fileobj(data, bucket, subFolder + fileName)

                        # remove local file after it has been created
                        os.remove(fileName)

                        print('\tSaved {} files for {} year {}'.format(file_type, companyName, year))

                except IndexError:
                    pass
            
        except TypeError:
            pass
            
        print('\nTime taken for loop in minutes is {}\n'.format((time.time() - startTime)/60))

In [ ]:
# call function to parse data from the SEC -> port to s3
fileExtract(secURLS, cik2brokers, bdNames)

0 - Downloading X-17A-5 files for ABRAHAM SECURITIES CORPORATION - CIK (1904)
	All files for ABRAHAM SECURITIES CORPORATION are downloaded

Time taken for loop in minutes is 0.029023114840189615

1 - Downloading X-17A-5 files for PROSPERA FINANCIAL SERVICES, INC. - CIK (2303)
	All files for PROSPERA FINANCIAL SERVICES, INC. are downloaded

Time taken for loop in minutes is 0.03576335112253825

2 - Downloading X-17A-5 files for AEI SECURITIES, INC. - CIK (2554)
	All files for AEI SECURITIES, INC. are downloaded

Time taken for loop in minutes is 0.04330683946609497

3 - Downloading X-17A-5 files for ALEXANDER INVESTMENT SERVICES CO. - CIK (3475)
	All files for ALEXANDER INVESTMENT SERVICES CO. are downloaded

Time taken for loop in minutes is 0.05194087425867717

4 - Downloading X-17A-5 files for ALLEN & COMPANY LLC - CIK (3683)
	All files for ALLEN & COMPANY LLC are downloaded

Time taken for loop in minutes is 0.06021300156911214

5 - Downloading X-17A-5 files for M. E. ALLISON & CO.,

44 - Downloading X-17A-5 files for K. W. CHAMBERS & CO. - CIK (19119)
	All files for K. W. CHAMBERS & CO. are downloaded

Time taken for loop in minutes is 0.34737396240234375

45 - Downloading X-17A-5 files for CHURCH, GREGORY, ADAMS SECURITIES CORPORATION - CIK (20195)
	All files for CHURCH, GREGORY, ADAMS SECURITIES CORPORATION are downloaded

Time taken for loop in minutes is 0.35803041855494183

46 - Downloading X-17A-5 files for ASSOCIATED INVESTMENT SERVICES, INC. - CIK (20502)
	All files for ASSOCIATED INVESTMENT SERVICES, INC. are downloaded

Time taken for loop in minutes is 0.3661477526028951

47 - Downloading X-17A-5 files for CLINGER & CO., INC. - CIK (21031)
	All files for CLINGER & CO., INC. are downloaded

Time taken for loop in minutes is 0.37220790386199953

48 - Downloading X-17A-5 files for OLD SLIP CAPITAL MANAGEMENT, INC. - CIK (21180)
	All files for OLD SLIP CAPITAL MANAGEMENT, INC. are downloaded

Time taken for loop in minutes is 0.3796322305997213

49 - Downlo

88 - Downloading X-17A-5 files for FMSBONDS, INC. - CIK (36520)
	All files for FMSBONDS, INC. are downloaded

Time taken for loop in minutes is 0.6904377539952596

89 - Downloading X-17A-5 files for FIRST MIDSTATE INC. - CIK (36528)
	All files for FIRST MIDSTATE INC. are downloaded

Time taken for loop in minutes is 0.696784234046936

90 - Downloading X-17A-5 files for COOMBE FINANCIAL SERVICES, INC. - CIK (36545)
	All files for COOMBE FINANCIAL SERVICES, INC. are downloaded

Time taken for loop in minutes is 0.7058672904968262

91 - Downloading X-17A-5 files for TD AMERITRADE CLEARING, INC. - CIK (36793)
	All files for TD AMERITRADE CLEARING, INC. are downloaded

Time taken for loop in minutes is 0.7124936660130818

92 - Downloading X-17A-5 files for CABRERA CAPITAL MARKETS, LLC - CIK (36882)
	All files for CABRERA CAPITAL MARKETS, LLC are downloaded

Time taken for loop in minutes is 0.7183698813120524

93 - Downloading X-17A-5 files for FOLGER NOLAN FLEMING DOUGLAS INCORPORATED - CI

131 - Downloading X-17A-5 files for SOMERSET SECURITIES, INC. - CIK (57106)
	All files for SOMERSET SECURITIES, INC. are downloaded

Time taken for loop in minutes is 0.9898515979448954

132 - Downloading X-17A-5 files for LADENBURG THALMANN & CO. INC. - CIK (57210)
	All files for LADENBURG THALMANN & CO. INC. are downloaded

Time taken for loop in minutes is 0.996236789226532

133 - Downloading X-17A-5 files for DEUTSCHE BANK SECURITIES INC. - CIK (58056)
	All files for DEUTSCHE BANK SECURITIES INC. are downloaded

Time taken for loop in minutes is 1.0042811036109924

134 - Downloading X-17A-5 files for LAZARD FRERES & CO. LLC - CIK (58124)
	All files for LAZARD FRERES & CO. LLC are downloaded

Time taken for loop in minutes is 1.010781180858612

135 - Downloading X-17A-5 files for M. H. LEBLANG, INC. - CIK (58290)
	All files for M. H. LEBLANG, INC. are downloaded

Time taken for loop in minutes is 1.0176847656567891

136 - Downloading X-17A-5 files for DAVID LERNER ASSOCIATES, INC. -

175 - Downloading X-17A-5 files for NATIONWIDE INVESTMENT SERVICES CORPORATION - CIK (76886)
	All files for NATIONWIDE INVESTMENT SERVICES CORPORATION are downloaded

Time taken for loop in minutes is 1.2920299172401428

176 - Downloading X-17A-5 files for AMERICAN TRUST INVESTMENT SERVICES, INC. - CIK (76964)
	All files for AMERICAN TRUST INVESTMENT SERVICES, INC. are downloaded

Time taken for loop in minutes is 1.301234535376231

177 - Downloading X-17A-5 files for HORNOR, TOWNSEND & KENT, LLC - CIK (77131)
	All files for HORNOR, TOWNSEND & KENT, LLC are downloaded

Time taken for loop in minutes is 1.3111598213513693

178 - Downloading X-17A-5 files for PFLUEGER & BAERWALD INC. - CIK (78017)
	All files for PFLUEGER & BAERWALD INC. are downloaded

Time taken for loop in minutes is 1.317095685005188

179 - Downloading X-17A-5 files for FBL MARKETING SERVICES, LLC - CIK (78027)
	All files for FBL MARKETING SERVICES, LLC are downloaded

Time taken for loop in minutes is 1.3252094427744

...

	Saved X-17A-5 files for WEALTH MONITORS, INC. year 2002

Time taken for loop in minutes is 600.6952563643456

5742 - Downloading X-17A-5 files for SOUTHEASTERN ADVISORY GROUP, INC. - CIK (779908)
	Saved X-17A-5 files for SOUTHEASTERN ADVISORY GROUP, INC. year 2012
	Saved X-17A-5 files for SOUTHEASTERN ADVISORY GROUP, INC. year 2011
	Saved X-17A-5 files for SOUTHEASTERN ADVISORY GROUP, INC. year 2010
	Saved X-17A-5 files for SOUTHEASTERN ADVISORY GROUP, INC. year 2009
	Saved X-17A-5 files for SOUTHEASTERN ADVISORY GROUP, INC. year 2008
	Saved X-17A-5 files for SOUTHEASTERN ADVISORY GROUP, INC. year 2007
	Saved X-17A-5 files for SOUTHEASTERN ADVISORY GROUP, INC. year 2007
	Saved X-17A-5 files for SOUTHEASTERN ADVISORY GROUP, INC. year 2006
	Saved X-17A-5 files for SOUTHEASTERN ADVISORY GROUP, INC. year 2005
	Saved X-17A-5 files for SOUTHEASTERN ADVISORY GROUP, INC. year 2004
	Saved X-17A-5 files for SOUTHEASTERN ADVISORY GROUP, INC. year 2003
	Saved X-17A-5 files for SOUTHEASTERN ADVISO

	Saved X-17A-5 files for DB SECURITIES SERVICES NJ INC. year 2011
	Saved X-17A-5 files for DB SECURITIES SERVICES NJ INC. year 2010
	Saved X-17A-5 files for DB SECURITIES SERVICES NJ INC. year 2009
	Saved X-17A-5 files for DB SECURITIES SERVICES NJ INC. year 2008

Time taken for loop in minutes is 601.8311090707779

5756 - Downloading X-17A-5 files for BLACKROCK FUND DISTRIBUTION COMPANY - CIK (1422727)
	Saved X-17A-5 files for BLACKROCK FUND DISTRIBUTION COMPANY year 2012
	Saved X-17A-5 files for BLACKROCK FUND DISTRIBUTION COMPANY year 2011
	Saved X-17A-5 files for BLACKROCK FUND DISTRIBUTION COMPANY year 2010
	Saved X-17A-5 files for BLACKROCK FUND DISTRIBUTION COMPANY year 2009
	Saved X-17A-5 files for BLACKROCK FUND DISTRIBUTION COMPANY year 2009

Time taken for loop in minutes is 601.8870024760564

5757 - Downloading X-17A-5 files for WINDFALL SECURITIES LLC - CIK (1438881)
	Saved X-17A-5 files for WINDFALL SECURITIES LLC year 2015
	Saved X-17A-5 files for WINDFALL SECURITIES LLC

	Saved X-17A-5 files for COMMONWEALTH ASSOCIATES year 2003
	Saved X-17A-5 files for COMMONWEALTH ASSOCIATES year 2002

Time taken for loop in minutes is 602.9202033321063

5769 - Downloading X-17A-5 files for WARREN D. NADEL & COMPANY - CIK (821573)
	Saved X-17A-5 files for WARREN D. NADEL & COMPANY year 2011
	Saved X-17A-5 files for WARREN D. NADEL & COMPANY year 2010
	Saved X-17A-5 files for WARREN D. NADEL & COMPANY year 2009
	Saved X-17A-5 files for WARREN D. NADEL & COMPANY year 2008
	Saved X-17A-5 files for WARREN D. NADEL & COMPANY year 2007
	Saved X-17A-5 files for WARREN D. NADEL & COMPANY year 2006
	Saved X-17A-5 files for WARREN D. NADEL & COMPANY year 2005
	Saved X-17A-5 files for WARREN D. NADEL & COMPANY year 2004
	Saved X-17A-5 files for WARREN D. NADEL & COMPANY year 2003
	Saved X-17A-5 files for WARREN D. NADEL & COMPANY year 2002

Time taken for loop in minutes is 603.0227022528649

5770 - Downloading X-17A-5 files for BOSTON MERCHANT FINANCIAL SERVICES, INC. - CIK (8

	Saved X-17A-5 files for WEISS CAPITAL SECURITIES, INC. year 2002

Time taken for loop in minutes is 603.9264677842458

5780 - Downloading X-17A-5 files for KIMBERLY CAPITAL CORP. - CIK (1018449)
	Saved X-17A-5 files for KIMBERLY CAPITAL CORP. year 2011
	Saved X-17A-5 files for KIMBERLY CAPITAL CORP. year 2010
	Saved X-17A-5 files for KIMBERLY CAPITAL CORP. year 2010
	Saved X-17A-5 files for KIMBERLY CAPITAL CORP. year 2009
	Saved X-17A-5 files for KIMBERLY CAPITAL CORP. year 2008
	Saved X-17A-5 files for KIMBERLY CAPITAL CORP. year 2007
	Saved X-17A-5 files for KIMBERLY CAPITAL CORP. year 2006
	Saved X-17A-5 files for KIMBERLY CAPITAL CORP. year 2005
	Saved X-17A-5 files for KIMBERLY CAPITAL CORP. year 2004
	Saved X-17A-5 files for KIMBERLY CAPITAL CORP. year 2003
	Saved X-17A-5 files for KIMBERLY CAPITAL CORP. year 2003
	Saved X-17A-5 files for KIMBERLY CAPITAL CORP. year 2002

Time taken for loop in minutes is 604.0432294209799

5781 - Downloading X-17A-5 files for IIG HORIZONS SECU

	Saved X-17A-5 files for FOX RIVER EXECUTION TECHNOLOGY, LLC year 2011
	Saved X-17A-5 files for FOX RIVER EXECUTION TECHNOLOGY, LLC year 2010
	Saved X-17A-5 files for FOX RIVER EXECUTION TECHNOLOGY, LLC year 2009
	Saved X-17A-5 files for FOX RIVER EXECUTION TECHNOLOGY, LLC year 2008
	Saved X-17A-5 files for FOX RIVER EXECUTION TECHNOLOGY, LLC year 2007
	Saved X-17A-5 files for FOX RIVER EXECUTION TECHNOLOGY, LLC year 2006

Time taken for loop in minutes is 604.9966025988261

5793 - Downloading X-17A-5 files for SCOTTISH RE CAPITAL MARKETS, INC - CIK (1327454)
	Saved X-17A-5 files for SCOTTISH RE CAPITAL MARKETS, INC year 2010
	Saved X-17A-5 files for SCOTTISH RE CAPITAL MARKETS, INC year 2009
	Saved X-17A-5 files for SCOTTISH RE CAPITAL MARKETS, INC year 2008
	Saved X-17A-5 files for SCOTTISH RE CAPITAL MARKETS, INC year 2007
	Saved X-17A-5 files for SCOTTISH RE CAPITAL MARKETS, INC year 2007

Time taken for loop in minutes is 605.0476277073225

5794 - Downloading X-17A-5 files for ALT